In [1]:
import pickle
import os
import google_auth_oauthlib.flow
import googleapiclient.discovery
import googleapiclient.errors
from google_auth_oauthlib.flow import InstalledAppFlow
from googleapiclient.discovery import build
from google.auth.transport.requests import Request
import json 

scopes = ["https://www.googleapis.com/auth/youtube.force-ssl"]

def Create_Service(client_secret_file, api_name, api_version, *scopes):
    print(client_secret_file, api_name, api_version, scopes, sep="-")
    CLIENT_SECRET_FILE = client_secret_file
    API_SERVICE_NAME = api_name
    API_VERSION = api_version
    SCOPES = [scope for scope in scopes[0]]
    print(SCOPES)
    cred = None
    pickle_file = f"token_{API_SERVICE_NAME}_{API_VERSION}.pickle"

    if os.path.exists(pickle_file):
        with open(pickle_file, "rb") as token:
            cred = pickle.load(token)

    if not cred or not cred.valid:
        if cred and cred.expired and cred.refresh_token:
            cred.refresh(Request())
        else:
            flow = InstalledAppFlow.from_client_secrets_file(CLIENT_SECRET_FILE, SCOPES)
            cred = flow.run_local_server()

        with open(pickle_file, "wb") as token:
            pickle.dump(cred, token)
            print("create token file ===>",pickle_file )

    try:
        service = build(API_SERVICE_NAME, API_VERSION, credentials=cred)
        print(API_SERVICE_NAME.capitalize(), "service created successfully.\n")
        return service
    except Exception as e:
        print("Unable to connect.")
        print(e)
        return None

#khởi tạo dịch vụ để sử dung Youtube API
os.environ["OAUTHLIB_INSECURE_TRANSPORT"] = "1"
api_service_name = "youtube"
api_version = "v3"
client_secrets_file = "client_secret_youtube.json"
#Tạo dịch vụ

service = Create_Service(client_secrets_file, api_service_name, api_version, scopes)


client_secret_youtube.json-youtube-v3-(['https://www.googleapis.com/auth/youtube.force-ssl'],)
['https://www.googleapis.com/auth/youtube.force-ssl']
create token file ===> token_youtube_v3.pickle
Youtube service created successfully.



In [3]:
# Lấy thông tin các video liên quan theo từ khóa tìm kiếm

allResponse = []
query = "chiến sự tại ukraine"# Sửa keyword để tìm kiếm tại đây

request = service.search().list(
    part="snippet",
    channelType="any",
    order="date",
    type="video",
    maxResults=50,
    q= query
)

more_pages = True

while(more_pages):
    response = request.execute()
    print(response)
    allResponse.append(response)
    next_page_token = response['nextPageToken']
    if next_page_token is None:
            more_pages = False
            break
    else:
        request = service.search().list(
            part="snippet",
            pageToken =  next_page_token,
            channelType="any",
            order="date",
            type="video",
            maxResults=50,
            q=query
        )
        
        

{'kind': 'youtube#searchListResponse', 'etag': '0eCXENScX0KGM7pGQxROnvQe_sY', 'nextPageToken': 'CDIQAA', 'regionCode': 'VN', 'pageInfo': {'totalResults': 1000000, 'resultsPerPage': 50}, 'items': [{'kind': 'youtube#searchResult', 'etag': 'i4xSmhIs3Ks67DBjP8YE6U8Rp6k', 'id': {'kind': 'youtube#video', 'videoId': 'tH6Mp6KXooY'}, 'snippet': {'publishedAt': '2024-03-06T22:00:26Z', 'channelId': 'UCo_ENbs21kd6DeJQV2UOi4A', 'title': 'tin tức 1 lữ đoàn của nga bị tiêu diệt /chiến sự tại ukraina #shorts', 'description': 'tin tức 1 lữ đoàn của nga bị tiêu diệt /chiến sự tại ukraina #shorts NỘI DUNG: mới đây , Một đoạn video khiến bạn xem không ...', 'thumbnails': {'default': {'url': 'https://i.ytimg.com/vi/tH6Mp6KXooY/default.jpg', 'width': 120, 'height': 90}, 'medium': {'url': 'https://i.ytimg.com/vi/tH6Mp6KXooY/mqdefault.jpg', 'width': 320, 'height': 180}, 'high': {'url': 'https://i.ytimg.com/vi/tH6Mp6KXooY/hqdefault.jpg', 'width': 480, 'height': 360}}, 'channelTitle': 'JOONG NGUYEN NEWS', 'live

KeyError: 'nextPageToken'

In [6]:
len(allResponse) #so page

import io

with io.open('result_all_page.json', 'w', encoding='utf-8') as f:
    json.dump(allResponse, f, ensure_ascii=False, indent=4)

In [7]:
from youtube_transcript_api import YouTubeTranscriptApi

result_all = []
for page in allResponse:
    response_items = page["items"]
    
    for itemvideo in response_items:
        if(itemvideo["id"]["kind"] == 'youtube#video'):
            #Lấy videoID để lấy captions của video
            videoid = itemvideo["id"]["videoId"]
            
            #Liệt kê ds các captions trong video và lấy captions tiếng việt
            transcript_fulltxt=[]
            try:
                transcript_list = YouTubeTranscriptApi.list_transcripts(videoid)
                for transcript in transcript_list:
                    #có thể sử ngôn ngữ đầu ra tại đây
                    transcript_fulltxt = transcript.translate('vi').fetch()
                onlyTrans = [item['text'] for item in transcript_fulltxt]
            except Exception as e:
                onlyTrans = []
                
            # Gom tất cả đoạn caption thành một chuỗi duy nhất
            if(len(onlyTrans) == 0):
                dataTrans = "Không lấy được captions"
            else:
                dataTrans = " ".join(onlyTrans)

            # dữ liệu tạm để lưu trữ 
            tempdata = {
                "videoId": itemvideo["id"]["videoId"],
                "publishedAt": itemvideo["snippet"]["publishedAt"],
                "title": itemvideo["snippet"]["title"],
                "channel" : {
                    "channelID": itemvideo["snippet"]["channelId"],
                    "channelTitle": itemvideo["snippet"]["channelTitle"],
                },
                "description" : itemvideo["snippet"]["description"],
                "captionData" : dataTrans
            }
            print(tempdata)
            result_all.append(tempdata)
            
            
            

{'videoId': 'tH6Mp6KXooY', 'publishedAt': '2024-03-06T22:00:26Z', 'title': 'tin tức 1 lữ đoàn của nga bị tiêu diệt /chiến sự tại ukraina #shorts', 'channel': {'channelID': 'UCo_ENbs21kd6DeJQV2UOi4A', 'channelTitle': 'JOONG NGUYEN NEWS'}, 'description': 'tin tức 1 lữ đoàn của nga bị tiêu diệt /chiến sự tại ukraina #shorts NỘI DUNG: mới đây , Một đoạn video khiến bạn xem không ...', 'captionData': 'mới đây một đoạn video khiến bạn xem không ngừng hồi hộp đến giây cuối cùng đoạn clip được người dân Ukraina chia sẻ trên cộng đồng mạng như sau đoàn xe tăng bradley từ lữ đoàn 47 omb của Ukraina đã ngăn chặn một cuộc tấn công khác của lữ đoàn vệ binh biệt động số 15 của Liên bang Nga một xe cơ giới đã bị nổ tung sau khi bỏ lại binh lính phục kích sau đó toàn bộ tiểu đội gồm 10 chiến binh này cũng đã h sinh tại biên giới Ukraina và Nga chiến trưng Ukraina và Nga vẫn còn nhiều điểm nóng liệu có sự thay đổi nào không hoạch chiến tranh có bị lang rộng sang những nước phương tây khác không Hãy đăn

TranscriptsDisabled: 
Could not retrieve a transcript for the video https://www.youtube.com/watch?v=sXneDSKGUzY! This is most likely caused by:

Subtitles are disabled for this video

If you are sure that the described cause is not responsible for this error and that a transcript should be retrievable, please create an issue at https://github.com/jdepoix/youtube-transcript-api/issues. Please add which version of youtube_transcript_api you are using and provide the information needed to replicate the error. Also make sure that there are no open issues which already describe your problem!

In [8]:
len(result_all)

144

In [9]:
with io.open('result_new_144.json', 'w', encoding='utf-8') as f:
    json.dump(result_all, f, ensure_ascii=False, indent=4)